# Pyomo teek
Pyomo on Pythoni teek formuleerimaks, lahendamaks ja analüüsimaks optimeerimismudeleid.

* Koduleht -- http://www.pyomo.org/documentation
* Dokumentatsioon -- https://pyomo.readthedocs.io/en/stable/

Optimeerimisülesannete lahendamiseks Pyomo'ga peame installeerima nii Pyomo kui ka mõne lahendaja ehk solveri.

Alljärgnevas näites installeerime Pyomo ja vabavaralise lahendaja 'GLPK' ehk [GNU Linear Programming Git](https://en.wikipedia.org/wiki/GNU_Linear_Programming_Kit)

In [1]:
# Installeerime Pyomo
!pip install -q pyomo

# Installeerime GLPK GNU Linear Programming Kit solveri
!apt-get install -y -qq glpk-utils -q

     |████████████████████████████████| 9.2 MB 21.9 MB/s 
     |████████████████████████████████| 49 kB 3.8 MB/s 
Selecting previously unselected package libsuitesparseconfig5:amd64.
(Reading database ... 155222 files and directories currently installed.)
Preparing to unpack .../libsuitesparseconfig5_1%3a5.1.2-2_amd64.deb ...
Unpacking libsuitesparseconfig5:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libamd2:amd64.
Preparing to unpack .../libamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libcolamd2:amd64.
Preparing to unpack .../libcolamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libcolamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libglpk40:amd64.
Preparing to unpack .../libglpk40_4.65-1_amd64.deb ...
Unpacking libglpk40:amd64 (4.65-1) ...
Selecting previously unselected package glpk-utils.
Preparing to unpack .../glpk-utils_4.65-1_amd64.deb ...
Unpacking glpk-utils (4.65-1) ...
Setting up

In [2]:
# Impordime Pyomo
import pyomo.environ as pyo

# Loome lahendaja klassi
solver = pyo.SolverFactory('glpk', executable='/usr/bin/glpsol')

# Tootmise optimeerimise ülesanne

Meil on tehas, kus toodame toodet X ja Y. 
* Oleme läbi viinud turuanalüüsi ja teame, et: 
    * toodet X suudaksime ühes nädalas müüa 40 ühikut hinnaga 270 €/tk. 
    * toodet Y suudaksime ühes nädalas müüa nii palju kui toota suudame hinnaga 210 €/tk.
* Kulude osas teame, et:    
    * Toote X tootmiseks kulub 100€ ulatuses toorainet, 1 tund vanemspetsialisti tööd ja 2 tundi nooremspetsialisti tööd.
    * Toote Y tootmiseks kulub 90€ ulatuses toorainet, 1 tund vanemspetsialisti tööd ja 1 tund nooremspetsialisti tööd.
* Palgad:
    * Vanemspetsialisti töötund maksab 50€/h
    * Nooremspetsialisti töötund maksab 40€/h
* Ressursipiirangud:
    * Toorainet saame kätte nii palju kui tahame.
    * Vanemspetsialist saab nädalas teha maksimaalselt 80 töötundi.
    * Nooremspetsialist saab nädalas teha maksimaalselt 100 töötundi.

Küsimus: Kui palju toodet X ja toodet Y peaksime me tootma, et maksimeerida oma kasum ning mis on kasumi suuruseks.

## Määratleme sisendandmed

In [4]:
# Toodete hinnad ja müügipiirangud
x_hind = 270
x_turupiirang = 40 #maksimumkogus, mida saame müüa
y_hind = 210

# Tooraine kulu ühe toote tootmiseks
x_tooraine = 100
y_tooraine = 90

# Tööjõu hinnad ja müügipiirangud
vanemspets_hind = 50
vanemspets_piirang = 80 #tundi nädalas
nooremspets_hind = 40
nooremspets_piirang = 100 #tundi nädalas

## Loome mudeli

In [3]:
# Loome mudeli
mudel = pyo.ConcreteModel()

## Lisame muutujad
Muutujad on need elemendid, mille õiget väärtust tahame leida. Antud juhul on muutujad toodete X ja Y kogused

In [5]:
# Loome muutujad ehk mille väärtust tahame leida
# Lisaks määratleme, et muutujad peavad kuuluma mittenegatiivsete arvude hulka
mudel.x = pyo.Var(domain=pyo.NonNegativeReals)
mudel.y = pyo.Var(domain=pyo.NonNegativeReals)

## Lisame piirangud
Igal optimeerimisülesandel on piirangud, millega me peame arvestama. Antud näites peame me arvestama turunõudluse ja saadaoleva tööjõuressursiga

In [8]:
# toodet x saame maksimaalselt müüa 40 ühikut nädalas
mudel.turg = pyo.Constraint(expr = mudel.x <= x_turupiirang)

# vanemspetsialisti tööaega on saada 80 tundi
# ja mõlema toote tootmiseks kulub üks tund vanemspetsialisti tööd
mudel.vanemspetsialist = pyo.Constraint(expr = mudel.x + mudel.y <= vanemspets_piirang)

#nooremspetsialisti tööaega on saada 100 tundi
# toote X tootmiseks kulub 2 ja toote Y tootmiseks 1 tund nooremspetsialisti tööd
mudel.nooremspetsialist = pyo.Constraint(expr = 2*mudel.x + mudel.y <= nooremspets_piirang)

## Defineerime eesmärgi
Meie eesmärgiks on maksimeerida kasum. Eesmärgina defineerime kasumifunktsiooni ja anname mudelile märku, et soovime seda maksimeerida `sense=pyo.maximize`

In [9]:
# Kui palju kasumit saame ühe toote tootmisest
kasum_x = x_hind - x_tooraine - vanemspets_hind - 2*nooremspets_hind
kasum_y = y_hind - y_tooraine - vanemspets_hind - nooremspets_hind 

# Eesmärk
mudel.kasum = pyo.Objective(expr = mudel.x*kasum_x + mudel.y*kasum_y, sense=pyo.maximize)
mudel.kasum.pprint()

    'pyomo.core.base.objective.ScalarObjective'>) on block unknown with a new
    Component (type=<class 'pyomo.core.base.objective.ScalarObjective'>). This
    is usually indicative of a modelling error. To avoid this warning, use
    block.del_component() and block.add_component().
kasum : Size=1, Index=None, Active=True
    Key  : Active : Sense    : Expression
    None :   True : maximize : 40*x + 30*y


## Lahendame ülesande

In [10]:
# Lahendame ülesande
solver.solve(mudel).write()

# ==========================================================
# = Solver Results                                         =
# ==========================================================
# ----------------------------------------------------------
#   Problem Information
# ----------------------------------------------------------
Problem: 
- Name: unknown
  Lower bound: 2600.0
  Upper bound: 2600.0
  Number of objectives: 1
  Number of constraints: 4
  Number of variables: 3
  Number of nonzeros: 6
  Sense: maximize
# ----------------------------------------------------------
#   Solver Information
# ----------------------------------------------------------
Solver: 
- Status: ok
  Termination condition: optimal
  Statistics: 
    Branch and bound: 
      Number of bounded subproblems: 0
      Number of created subproblems: 0
  Error rc: 0
  Time: 0.023662805557250977
# ----------------------------------------------------------
#   Solution Information
# ----------------------------------

## Vaatame tulemusi

In [11]:
print("Optimaalne tootmisplaan:\n")
print("Toote X kogus = ", mudel.x())
print("Toote Y kogus = ", mudel.y())
print("Kasum = ", mudel.kasum())

Optimaalne tootmisplaan:

Toote X kogus =  20.0
Toote Y kogus =  60.0
Kasum =  2600.0


# Teeme optimeerimisfunktsiooni

In [12]:
def toodangu_optimeerija(
    x_hind = 270, 
    x_turupiirang = 40, 
    y_hind = 210, 
    y_turupiirang = None,
    x_tooraine = 100,
    y_tooraine = 90,
    vanemspets_hind = 50,
    vanemspets_piirang = 80,
    nooremspets_hind = 40,
    nooremspets_piirang = 100
    ):
    """
    See on funktsioon, mis leiab sulle tootmiskogused, millega saad maksimaalse kasumi.
    """
    # Loome mudeli
    mudel = pyo.ConcreteModel()

    # Loome muutujad ehk mille väärtust tahame leida
    mudel.x = pyo.Var(domain=pyo.NonNegativeReals)
    mudel.y = pyo.Var(domain=pyo.NonNegativeReals)

    # PIIRANGUD
    mudel.x_turg = pyo.Constraint(expr = mudel.x <= x_turupiirang)
    if y_turupiirang:
        mudel.y_turg = pyo.Constraint(expr = mudel.y <= y_turupiirang)
    mudel.vanemspetsialist = pyo.Constraint(expr = mudel.x + mudel.y <= vanemspets_piirang)
    mudel.nooremspetsialist = pyo.Constraint(expr = 2*mudel.x + mudel.y <= nooremspets_piirang)

    # EESMÄRK
    # Kui palju kasumit saame ühe toote tootmisest
    kasum_x = x_hind - x_tooraine - vanemspets_hind - 2*nooremspets_hind
    kasum_y = y_hind - y_tooraine - vanemspets_hind - nooremspets_hind 
    mudel.kasum = pyo.Objective(expr = mudel.x*kasum_x + mudel.y*kasum_y, sense=pyo.maximize)

    # Lahendame
    solver.solve(mudel)

    print("Optimaalne tootmisplaan:\n")
    print("Toote X kogus = ", mudel.x())
    print("Toote Y kogus = ", mudel.y())
    print("Kasum = ", mudel.kasum())

## Proovime funktsiooni

In [13]:
toodangu_optimeerija()

Optimaalne tootmisplaan:

Toote X kogus =  20.0
Toote Y kogus =  60.0
Kasum =  2600.0


# Mängime stsenaariumitega

## Toote X müügihinna tõus
Soodsate turutingimuste tõttu saame tõsta toote X müügihinna 290 euroni. Mis on optimaalne tootmisplaan nüüd?

In [14]:
toodangu_optimeerija(x_hind=290)

Optimaalne tootmisplaan:

Toote X kogus =  40.0
Toote Y kogus =  20.0
Kasum =  3000.0


## Tooraine kallinemine
Toote X tooraine kallines 115 euroni ja Toote Y tooraine kallines 97 euroni.

In [15]:
toodangu_optimeerija(x_tooraine=115, y_tooraine=97)

Optimaalne tootmisplaan:

Toote X kogus =  20.0
Toote Y kogus =  60.0
Kasum =  1880.0


## Vanemspetsialisti puhkus
Järgmisel nädalal on vanemspetsialist poolest nädalast puhkusel ja tema aega on kokku saada 50 tundi.

In [16]:
toodangu_optimeerija(vanemspets_piirang=50)

Optimaalne tootmisplaan:

Toote X kogus =  40.0
Toote Y kogus =  10.0
Kasum =  1900.0


## Nooremspetsialisti palgatõus
Nooremspetsialist küsib palka juurde ja tema tunnikulu tõuseb 45 € peale.

In [17]:
toodangu_optimeerija(nooremspets_hind=45)

Optimaalne tootmisplaan:

Toote X kogus =  20.0
Toote Y kogus =  60.0
Kasum =  2100.0
